# Analysis of Neural Programmer

In [1]:
import copy
import itertools
import operator
import os
import pickle
import re
import string
import sys
import time
from collections import Counter, defaultdict
from random import shuffle

import autoreload
import matplotlib.pyplot as plt
import nltk
import numpy as np
import pandas as pd
import seaborn as sns
import tensorflow as tf
from IPython.display import HTML, Image, clear_output, display
from scipy.spatial.distance import cosine

sys.path.append('../neural_programmer')

/scratch/pramodkm/tensorflow_gpu_python3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
import notebook_utils
import data_utils
from neural_programmer import evaluate

In [3]:
%reload_ext autoreload
%autoreload 2

## Paths, parameters, etc. 

In [4]:
# Use only one GPU on the multi-GPU machine
os.environ["CUDA_VISIBLE_DEVICES"] = "0-3"

# WikiTableQuestions data
DATA_DIR = '../wtq_data'
PERTURBED_DATA_DIR = '../perturbed_wtq_data'

# Pretrained model
MODEL_FILE = os.path.join('..', 'pretrained_model', 'model_92500')
model_step = int(MODEL_FILE.split('_')[-1])

# Output directory to write attributions
OUT_DIR = '../results'

# Overstability curve file
OVERSTABILITY_CURVE_FILE = os.path.join(OUT_DIR, 'overstability.eps')

## Load data, build graph and restore pretrained weights

In [6]:
train_data, dev_data, test_data, utility = notebook_utils.init_data(DATA_DIR)

('Annotated examples loaded ', 14152)
('Annotated examples loaded ', 4344)
('entry match token: ', 9133, 9133)
('entry match token: ', 9134, 9134)
('# train examples ', 10178)
('# dev examples ', 2546)
('# test examples ', 3913)


In [7]:
tf.reset_default_graph()
sess, graph, params = notebook_utils.build_graph(utility)

forget gate bias
('step: ', 0)
('step: ', 1)
('step: ', 2)
('step: ', 3)
('optimize params ', ['unit', 'word', 'word_match_feature_column_name', 'controller', 'column_controller', 'column_controller_prev', 'controller_prev', 'question_lstm_ix', 'question_lstm_fx', 'question_lstm_cx', 'question_lstm_ox', 'question_lstm_im', 'question_lstm_fm', 'question_lstm_cm', 'question_lstm_om', 'question_lstm_i', 'question_lstm_f', 'question_lstm_c', 'question_lstm_o', 'history_recurrent', 'history_recurrent_bias', 'break_conditional'])
('grads: ', <tf.Tensor 'gradients_40/L2Loss_grad/mul:0' shape=(15, 256) dtype=float64>, 'unit')
('grads: ', <tf.Tensor 'gradients_40/L2Loss_1_grad/mul:0' shape=(10800, 256) dtype=float64>, 'word')
('grads: ', <tf.Tensor 'gradients_40/L2Loss_2_grad/mul:0' shape=(1,) dtype=float64>, 'word_match_feature_column_name')
('grads: ', <tf.Tensor 'gradients_40/L2Loss_3_grad/mul:0' shape=(512, 256) dtype=float64>, 'controller')
('grads: ', <tf.Tensor 'gradients_40/L2Loss_4_gra

In [8]:
sess, graph = notebook_utils.restore_model(sess, graph, params, MODEL_FILE)

INFO:tensorflow:Restoring parameters from ../pretrained_model/model_92500


In [8]:
num_correct, num_examples, correct_dict = evaluate(sess, dev_data, utility.FLAGS.batch_size, graph, model_step)

('dev set accuracy   after ', 92500, ' : ', 0.37195600942655144)
(2546, 2546)
--------


In [9]:
num_correct/2831.0

0.3345107735782409

## Apply Integrated Gradients (IG) 

In [34]:
# write attributions to this folder
attrs_outdir = os.path.join(OUT_DIR, 'attributions')
if not os.path.isdir(attrs_outdir):
    os.makedirs(attrs_outdir)

# get embedding of dummy token
embeddings = graph.params["word"].eval()
dummy_embedding = embeddings[utility.dummy_token_id, :]

# which data to use?
data = dev_data

# number of sample points for Riemann integral computation
num_points = 2000

# hard coded stuff in the code
question_attention_mask_value = -10000.0

In [ ]:
batch_size = graph.batch_size

for offset in range(0, len(data) - graph.batch_size + 1, graph.batch_size):
    feed_dict = data_utils.generate_feed_dict(data, offset, graph.batch_size, graph)

    # first run inference to get operator and column sequences, and embeddings of question words
    fetches = [graph.final_correct_list, graph.final_operation_softmax,
               graph.final_column_softmax, graph.question_words_embeddings]
    correct_list, operation_softmax, column_softmax, question_words_embeddings = sess.run(
        fetches, feed_dict)

    # compute table-specific default programs for tables in this batch
    feed_copy = feed_dict.copy()
    for t in graph.question_words_embeddings:
        feed_copy[t] = np.concatenate(
            [np.expand_dims(dummy_embedding, 0)]*batch_size, 0)

    # Ideally the following line should be uncommented, but for attributions,
    # we choose to keep this variable fixed. Note that this induces some bias
    # in the attributions as the baseline is no longer an "empty" question, but
    # an empty question where the question length is implicitly encoded in this variable
    # feed_copy[graph.batch_question_attention_mask].fill(question_attention_mask_value)

    feed_copy[graph.batch_exact_match] = np.zeros_like(
        feed_copy[graph.batch_exact_match])
    feed_copy[graph.batch_column_exact_match] = np.zeros_like(
        feed_copy[graph.batch_column_exact_match])

    fetches = [graph.final_operation_softmax, graph.final_column_softmax]

    default_operation_softmax, default_column_softmax = sess.run(
        fetches, feed_copy)

    for batch_id in range(batch_size):
        wiki_example = data[offset+batch_id]

        # get operator indices
        op_indices = np.argmax(operation_softmax[batch_id, :, :], axis=1)
        col_indices = np.argmax(column_softmax[batch_id, :, :], axis=1)

        op_list = notebook_utils.softmax_to_names(
            operation_softmax[batch_id, :, :], utility.operations_set)
        col_list = notebook_utils.softmax_to_names(
            column_softmax[batch_id, :, :], notebook_utils.get_column_names(wiki_example))

        default_op_list = notebook_utils.softmax_to_names(
            default_operation_softmax[batch_id, :, :], utility.operations_set)
        default_col_list = notebook_utils.softmax_to_names(
            default_column_softmax[batch_id, :, :], notebook_utils.get_column_names(wiki_example))

        print([notebook_utils.rename(w) for w in op_list])
        print(col_list)

        # Sample points along the integral path and collect them as one batch
        scaled_feed = feed_dict.copy()
        for key in list(scaled_feed.keys()):
            value = feed_dict[key]
            if key.shape[0] == batch_size:  # this is a hack
                scaled_feed[key] = [value[batch_id] for i in range(batch_size)]
        scaled_feed[graph.op_ids] = op_indices
        scaled_feed[graph.col_ids] = col_indices

        num_examples = batch_size * int(num_points/float(batch_size))
        scale = 1.0/num_examples

        batch_op_attribution = np.zeros(
            [graph.max_passes, graph.question_length+2], dtype=np.float32)
        batch_col_attribution = np.zeros(
            [graph.max_passes, graph.question_length+2], dtype=np.float32)

        attr_op_softmax = []
        attr_col_softmax = []

        actual_num_numeric_cols = len(wiki_example.original_nc_names)
        actual_num_word_cols = len(wiki_example.original_wc_names)

        exact_match = wiki_example.exact_match
        exact_column_match = wiki_example.exact_column_match

        batch_question_embeddings = np.array(question_words_embeddings)[
            :, batch_id, :]  # shape: 62 x 256

        # split up set of points into batch_size'd batches
        for k in range(0, num_examples, batch_size):
            print('k:', k)
            # scale question words to points between dummy_embedding and actual embedding
            qw_jump = [None]*graph.question_length
            for i, t in enumerate(graph.question_words_embeddings):
                qw_jump[i] = scale * \
                    (batch_question_embeddings[i] - dummy_embedding)
                scaled_feed[t] = [dummy_embedding + j*qw_jump[i]
                                  for j in range(k, k+batch_size)]

            # scale batch_exact_match
            scaled_exact_match = []
            scaled_column_exact_match = []

            exact_match_jump = [None]*(graph.num_cols + graph.num_word_cols)
            exact_column_match_jump = [None] * \
                (graph.num_cols + graph.num_word_cols)
            for i in range(graph.num_cols):
                if i < actual_num_numeric_cols:  # do not scale dummy columns
                    scaled_exact_match.append(np.expand_dims(
                        [j*scale*np.array(exact_match[i]) for j in range(k, k+batch_size)], 1))
                    exact_match_jump[i] = scale*np.array(exact_match[i])
                    scaled_column_exact_match.append(np.expand_dims(
                        [j*scale*np.array(exact_column_match[i]) for j in range(k, k+batch_size)], 1))
                    exact_column_match_jump[i] = scale * \
                        np.array(exact_column_match[i])
                else:
                    scaled_exact_match.append(np.expand_dims(
                        [exact_match[i] for j in range(k, k+batch_size)], 1))
                    exact_match_jump[i] = 0
                    scaled_column_exact_match.append(np.expand_dims(
                        [exact_column_match[i] for j in range(k, k+batch_size)], 1))
                    exact_column_match_jump[i] = 0

            for i in range(graph.num_word_cols):
                if i < actual_num_word_cols:  # do not scale dummy column names
                    scaled_exact_match.append(np.expand_dims(
                        [j*scale*np.array(exact_match[graph.num_cols+i]) for j in range(k, k+batch_size)], 1))
                    exact_match_jump[graph.num_cols + i] = scale * \
                        np.array(exact_match[graph.num_cols+i])
                    scaled_column_exact_match.append(np.expand_dims(
                        [j*scale*np.array(exact_column_match[graph.num_cols + i]) for j in range(k, k+batch_size)], 1))
                    exact_column_match_jump[graph.num_cols + i] = scale * \
                        np.array(exact_column_match[graph.num_cols + i])
                else:
                    scaled_exact_match.append(np.expand_dims(
                        [exact_match[graph.num_cols+i] for j in range(k, k+batch_size)], 1))
                    exact_match_jump[graph.num_cols + i] = 0
                    scaled_column_exact_match.append(np.expand_dims(
                        [exact_column_match[graph.num_cols + i] for j in range(k, k+batch_size)], 1))
                    exact_column_match_jump[graph.num_cols + i] = 0

            scaled_feed[graph.batch_exact_match] = np.concatenate(
                scaled_exact_match, 1)  # shape 20 x 40 x 100
            scaled_feed[graph.batch_column_exact_match] = np.concatenate(
                scaled_column_exact_match, 1)  # shape 20 x 40

            # compute gradients
            fetches = [graph.final_operation_softmax, graph.final_column_softmax, graph.operator_gradients,
                       graph.column_gradients]
            temp_op_softmax, temp_col_softmax, operator_gradients, column_gradients = sess.run(
                fetches, scaled_feed)  # operator gradient shape: 4 x 62 x 20 x 256

            attr_op_softmax.append(temp_op_softmax)
            attr_col_softmax.append(temp_col_softmax)

            # compute attributions
            for stage in range(graph.max_passes):
                n = int(len(operator_gradients)/graph.max_passes)
                temp = [np.sum(operator_gradients[n*stage][i]*qw_jump[i], axis=(0, 1))
                        for i in range(graph.question_length)]
                temp += [np.sum([operator_gradients[n*stage+1][0][:, i, :]*exact_match_jump[i]
                                 for i in range(graph.num_cols + graph.num_word_cols)])]
                temp += [np.sum([operator_gradients[n*stage+2][0][:, i]*exact_column_match_jump[i]
                                 for i in range(graph.num_cols + graph.num_word_cols)])]
                batch_op_attribution[stage, :] += temp

            for stage in range(graph.max_passes):
                n = int(len(column_gradients)/graph.max_passes)
                temp = [np.sum(column_gradients[n*stage][i]*qw_jump[i], axis=(0, 1))
                        for i in range(graph.question_length)]
                temp += [np.sum([column_gradients[n*stage+1][0][:, i, :]*exact_match_jump[i]
                                 for i in range(graph.num_cols + graph.num_word_cols)])]
                temp += [np.sum([column_gradients[n*stage+2][0][:, i]*exact_column_match_jump[i]
                                 for i in range(graph.num_cols + graph.num_word_cols)])]
                batch_col_attribution[stage, :] += temp

        # sanity check to make sure the integral summation adds up to function difference
        attr_op_softmax = np.concatenate(attr_op_softmax, axis=0)
        attr_col_softmax = np.concatenate(attr_col_softmax, axis=0)
        for stage in range(graph.max_passes):
            lhs = np.sum(batch_op_attribution[stage, :])
            input_fn_value = operation_softmax[batch_id,
                                               stage, op_indices[stage]]
            baseline_fn_value = attr_op_softmax[0, stage, op_indices[stage]]
            rhs = input_fn_value - baseline_fn_value
            print('OP', stage, ':', 'baseline=', baseline_fn_value, ', input_fn=',
                  input_fn_value, 'check: ', lhs, ' - ', rhs, ' = ', lhs-rhs)
        for stage in range(graph.max_passes):
            lhs = np.sum(batch_col_attribution[stage, :])
            input_fn_value = column_softmax[batch_id,
                                            stage, col_indices[stage]]
            baseline_fn_value = attr_col_softmax[0, stage, col_indices[stage]]
            rhs = input_fn_value - baseline_fn_value
            print('COL', stage, ':', 'baseline=', baseline_fn_value, ', input_fn=',
                  input_fn_value, 'check: ', lhs, ' - ', rhs, ' = ', lhs-rhs)

        op_attributions = [None]*graph.max_passes
        question_begin = np.nonzero(
            wiki_example.question_attention_mask)[0].shape[0]

        attributions_matrix = np.zeros(
            [graph.question_length - question_begin + 2, 2 * graph.max_passes])
        row_labels = []  # question words, tm, cm
        col_labels = []  # operator and column selections
        col_label_softmaxes = []  # softmaxes of the selections

        for ix in range(question_begin, graph.question_length):
            word = utility.reverse_word_ids[wiki_example.question[ix]]
            if word == utility.unk_token:
                word = word + '-' + [str(w) for w in wiki_example.string_question if w !=
                                     wiki_example.question_number and w != wiki_example.question_number_1][ix - question_begin]
            word = notebook_utils.rename(word)
            row_labels.append(word)
        row_labels.extend(['tm', 'cm'])

        for stage in range(graph.max_passes):
            col_labels.append(notebook_utils.rename(
                op_list[stage]) + ' (' + notebook_utils.rename(default_op_list[stage]) + ')')
            col_labels.append(notebook_utils.rename(
                col_list[stage]) + ' (' + notebook_utils.rename(default_col_list[stage]) + ')')

            col_label_softmaxes.append(str(operation_softmax[batch_id, stage, op_indices[stage]]) + ' (' + str(
                default_operation_softmax[batch_id, stage, op_indices[stage]]) + ')')
            col_label_softmaxes.append(str(column_softmax[batch_id, stage, col_indices[stage]]) + ' (' + str(
                default_column_softmax[batch_id, stage, col_indices[stage]]) + ')')

            attributions_matrix[:, 2 * stage] = batch_op_attribution[stage, question_begin:]
            attributions_matrix[:, 2 * stage +
                                1] = batch_col_attribution[stage, question_begin:]

        question_string = ' '.join([notebook_utils.rename(str(w))
                                    for w in wiki_example.string_question])

        # save operator and column selections to file
        with tf.gfile.GFile(os.path.join(attrs_outdir, wiki_example.question_id + '_labels.tsv'), 'w') as outf:
            outf.write(question_string)
            outf.write('\n')
            outf.write(str(correct_list[batch_id] == 1.0))
            outf.write('\n')
            outf.write('\t'.join(row_labels) + '\n')
            outf.write('\t'.join(col_labels) + '\n')
            outf.write('\t'.join(col_label_softmaxes) + '\n')

        # save attributions to file
        np.savetxt(os.path.join(
            attrs_outdir, wiki_example.question_id + '_attrs.txt'), attributions_matrix)


['select', 'prev', 'first', 'print']
['team', 'team', 'wins', 'team']
k: 0
k: 20
k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.18709323784186127 , input_fn= 0.9895706953516668 check:  0.8025567  -  0.8024774575098055  =  7.923604411907981e-05
OP 1 : baseline= 0.000754526421322655 , input_fn= 0

k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.1870936907940413 , input_fn= 0.9596679880832044 check:  0.7725198  -  0.7725742972891632  =  -5.447040012507287e-05
OP 1 : baseline= 0.0008520387693544778 , input_fn= 0.9871788168624861 check:  0.98637307  -  0.9863267780931316  =  4.628880902901589e-05
OP 2 : baseline= 0.23724541416596998 , input_fn= 0.6515535478285148 check:  0.41450986  -  0.4143081336625448  =  0.00020172899881687467
OP 3 : baseline= 0.9916130055873466 , input_fn= 0.999997689439334 check:  0.00839164  -  0.008384683851987429  =  6.956297069482531e-06
COL 0 : baseline= 0.9848173617953253 , input_fn= 0.8399076024408553 check:  -0.14493178  -  -0.14490975935447004  =  -2.20189572593954e-05
COL

k: 20
k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.18709525395991572 , input_fn= 0.9779964183932602 check:  0.79098296  -  0.7909011644333446  =  8.179722131851364e-05
OP 1 : baseline= 0.005860701074038522 , input_fn= 0.9810094645519328 check:  0.97515863  -  0.9751487634778943  =  9.86832371

k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.18709718396071368 , input_fn= 0.6312753676449212 check:  0.44407627  -  0.44417818368420753  =  -0.00010191381917151743
OP 1 : baseline= 0.00014811376105151067 , input_fn= 0.9556058744309084 check:  0.9554415  -  0.9554577606698569  =  -1.6285755306100214e-05
OP 2 : baseline= 0.0677029596929905 , input_fn= 0.9761918044701157 check:  0.908052  -  0.9084888447771251  =  -0.00043681755163071934
OP 3 : baseline= 0.30487587304618163 , input_fn= 0.9394405901700019 check:  0.63445884  -  0.6345647171238202  =  -0.00010587723047916775
COL 0 : baseline= 0.0731714670996283 , input_fn= 0.999989517794274 check:  0.9269154  -  0.9268180506946457  =  9.73564861403986e-05
COL 1 : baseline= 0.036062835360386555 , input_fn= 1.0 check:  0.96459264  -  0.96393716463

k: 20
k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.42256055445631374 , input_fn= 0.3824343083371853 check:  -0.040206105  -  -0.04012624611912846  =  -7.985839785457083e-05
OP 1 : baseline= 0.09012546876964628 , input_fn= 0.4375909892268931 check:  0.347355  -  0.3474655204572468  =  -0.00011

...

k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.18709957587073608 , input_fn= 0.33994149767641335 check:  0.15259159  -  0.15284192180567727  =  -0.0002503356927011924
OP 1 : baseline= 0.13290389389829338 , input_fn= 0.4478243379805211 check:  0.31485212  -  0.31492044408222775  =  -6.832559010128136e-05
OP 2 : baseline= 0.8755246536411658 , input_fn= 0.5398152171245881 check:  -0.3362411  -  -0.3357094365165777  =  -0.0005316597415857549
OP 3 : baseline= 0.9999001659345214 , input_fn= 0.9960202601718157 check:  -0.0038790745  -  -0.003879905762705693  =  8.312897716855616e-07
COL 0 : baseline= 0.2521347814930829 , input_fn= 0.9972159597441614 check:  0.74539274  -  0.7450811782510786  =  0.0003115615217180734
COL 1 : baseline= 0.024057377374930914 , input_fn= 0.

k: 20
k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.18709718396071368 , input_fn= 0.9092930457311552 check:  0.72194594  -  0.7221958617704416  =  -0.000249920322229924
OP 1 : baseline= 0.016516510618966983 , input_fn= 0.6880927878157953 check:  0.67072016  -  0.6715762771968283  =  -0.0008561

k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.1870946962075305 , input_fn= 0.9631925790177766 check:  0.776054  -  0.776097882810246  =  -4.385811389595595e-05
OP 1 : baseline= 0.00015082019907300292 , input_fn= 0.9821237183932379 check:  0.9816737  -  0.9819728981941649  =  -0.00029918069538559244
OP 2 : baseline= 0.013274736255788754 , input_fn= 0.9971027780389897 check:  0.9842775  -  0.9838280417832009  =  0.0004494450179465259
OP 3 : baseline= 0.04664867148230105 , input_fn= 0.9806015652913018 check:  0.9349042  -  0.9339528938090008  =  0.0009513239110309213
COL 0 : baseline= 0.005031112177962705 , input_fn= 1.0 check:  0.9949919  -  0.9949688878220373  =  2.3010714644833286e-05
COL 1 : baseline= 0.000878096736345493 , input_fn= 1.0 check:  0.9980163  -  

k: 20
k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.42255032360335654 , input_fn= 0.8155374254933367 check:  0.39279652  -  0.3929871018899802  =  -0.00019058547152317473
OP 1 : baseline= 0.6443457659051526 , input_fn= 0.9638333141044355 check:  0.32013357  -  0.31948754819928293  =  0.0006460

k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.1870946962075305 , input_fn= 0.3440368603392177 check:  0.15673265  -  0.1569421641316872  =  -0.00020951552061848622
OP 1 : baseline= 0.10864947720629324 , input_fn= 0.6911215676753347 check:  0.5817846  -  0.5824720904690415  =  -0.0006874844891220366
OP 2 : baseline= 0.12509446215926562 , input_fn= 0.33248739082658285 check:  0.20709956  -  0.20739292866731723  =  -0.00029337174440463576
OP 3 : baseline= 0.7975880967641078 , input_fn= 0.9996580643086291 check:  0.20229727  -  0.20206996754452133  =  0.00022730275348281648
COL 0 : baseline= 0.20409392955705888 , input_fn= 0.9971986214144968 check:  0.7934545  -  0.7931046918574379  =  0.00034983599748150684
COL 1 : baseline= 0.14361

## Create HTML with visualizations

In [42]:
data = dev_data
figs_outdir = os.path.join(OUT_DIR, "heatmaps")
if not os.path.isdir(figs_outdir):
    os.makedirs(figs_outdir)

In [ ]:
for wiki_example in data[:int(len(data)/graph.batch_size)]:
    attributions = np.loadtxt(os.path.join(attrs_outdir, wiki_example.question_id + '_attrs.txt'))
    with tf.gfile.GFile(os.path.join(attrs_outdir, wiki_example.question_id + '_labels.tsv')) as f:
        lines = f.readlines()
        xlabels = ['\n'.join(w.split()) for w in lines[3].strip().split('\t')]
        ylabels = lines[2].strip().split('\t')
    plt.figure(figsize=(len(xlabels),len(ylabels)/2))
    sns.heatmap(attributions, xticklabels=xlabels, yticklabels=ylabels, annot=True, fmt=".3f", robust=True)
    plt.tight_layout()
    plt.savefig(os.path.join(figs_outdir, wiki_example.question_id + '.png'))
    plt.close()

In [ ]:
with tf.gfile.GFile(os.path.join(OUT_DIR, 'visualizations.html'), 'w') as htmlf:
    htmlf.write()
    for wiki_example in data[:int(len(data)/graph.batch_size)]:


## Apply Integrated Gradients on table-specific default programs

In [56]:
# write attributions to this file
attrs_outdir = os.path.join(OUT_DIR, 'attributions_default_programs')
if not os.path.isdir(attrs_outdir):
    os.makedirs(attrs_outdir)

# get embedding of dummy token
embeddings = graph.params["word"].eval()
dummy_embedding = embeddings[utility.dummy_token_id, :]

# which data to use?
data = copy.deepcopy(dev_data)

# number of sample points for Riemann integral computation
num_points = 2000

# hard coded stuff in the code
question_attention_mask_value = -10000.0

In [57]:
# collect all unique tables
unique_tables = {}
for wiki_example in data:
    if not wiki_example.table_key in unique_tables:
        wiki_example.exact_column_match = np.zeros_like(
            wiki_example.exact_column_match).tolist()
        wiki_example.exact_match = np.zeros_like(
            wiki_example.exact_match).tolist()
        wiki_example.question = [
            utility.dummy_token_id] * graph.question_length
        wiki_example.question_attention_mask = (question_attention_mask_value * \
            np.ones_like(wiki_example.question_attention_mask)).tolist()
        unique_tables[wiki_example.table_key] = wiki_example
data = list(unique_tables.values())

In [59]:
for offset in range(0, len(data) - graph.batch_size + 1, batch_size):

    feed_dict = data_utils.generate_feed_dict(data, offset, batch_size, graph)
    fetches = [graph.final_correct_list, graph.final_operation_softmax,
               graph.final_column_softmax, graph.column_hidden_vectors, graph.word_column_hidden_vectors]
    correct_list, operation_softmax, column_softmax, column_hidden_vectors, word_column_hidden_vectors = sess.run(
        fetches, feed_dict)

    # compute global default program
    feed_copy = feed_dict.copy()
    feed_copy[graph.column_hidden_vectors] = np.zeros(
        graph.column_hidden_vectors.get_shape().as_list())
    feed_copy[graph.word_column_hidden_vectors] = np.zeros(
        graph.word_column_hidden_vectors.get_shape().as_list())
    default_operation_softmax, default_column_softmax = sess.run([graph.final_operation_softmax, graph.final_column_softmax], feed_copy)

    for batch_id in range(batch_size):
        wiki_example = data[offset + batch_id]

        # get op indices
        op_indices = np.argmax(operation_softmax[batch_id, :, :], axis=1)
        col_indices = np.argmax(column_softmax[batch_id, :, :], axis=1)

        op_list = notebook_utils.softmax_to_names(
            operation_softmax[batch_id, :, :], utility.operations_set)
        col_list = notebook_utils.softmax_to_names(
            column_softmax[batch_id, :, :], notebook_utils.get_column_names(wiki_example))

        print([notebook_utils.rename(w) for w in op_list])
        print(col_list)

        # generate scaled feed
        scaled_feed = feed_dict.copy()
        for key in list(scaled_feed.keys()):
            value = feed_dict[key]
            if key.shape[0] == batch_size: # this is a hack
                scaled_feed[key] = [value[batch_id] for i in range(batch_size)]
        scaled_feed[graph.op_ids] = op_indices
        scaled_feed[graph.col_ids] = col_indices

        num_examples = batch_size * int(num_points/float(batch_size))
        scale = 1.0 / num_examples

        batch_op_attribution = np.zeros(
            [graph.max_passes, graph.num_cols + graph.num_word_cols], dtype=np.float32)
        batch_col_attribution = np.zeros(
            [graph.max_passes, graph.num_cols + graph.num_word_cols], dtype=np.float32)
        
        attr_op_softmax = []
        attr_col_softmax = []

        actual_num_numeric_cols = len(wiki_example.original_nc_names)
        actual_num_word_cols = len(wiki_example.original_wc_names)
        numeric_column_name_jump = [None] * graph.num_cols
        word_column_name_jump = [None] * graph.num_word_cols
        for k in range(0, num_examples, batch_size):
            print('k:', k)
            scaled_numeric_column_names = []
            scaled_word_column_names = []

            for i in range(graph.num_cols):
                if i < actual_num_numeric_cols:  # do not scale dummy column
                    scaled_numeric_column_names.append(np.expand_dims(
                        [j * scale * np.array(column_hidden_vectors[batch_id, i, :]) for j in range(k, k + batch_size)], 1))
                    numeric_column_name_jump[i] = scale * \
                        np.array(column_hidden_vectors[batch_id, i, :])
                else:
                    scaled_numeric_column_names.append(np.expand_dims([np.array(
                        column_hidden_vectors[batch_id, i, :]) for j in range(k, k + batch_size)], 1))
                    numeric_column_name_jump[i] = 0

            for i in range(graph.num_word_cols):
                if i < actual_num_word_cols:  # do not scale dummy column names
                    scaled_word_column_names.append(np.expand_dims(
                        [j * scale * np.array(word_column_hidden_vectors[batch_id, i, :]) for j in range(k, k + batch_size)], 1))
                    word_column_name_jump[i] = scale * \
                        np.array(word_column_hidden_vectors[batch_id, i, :])
                else:
                    scaled_word_column_names.append(np.expand_dims([np.array(
                        word_column_hidden_vectors[batch_id, i, :]) for j in range(k, k + batch_size)], 1))
                    word_column_name_jump[i] = 0

            scaled_feed[graph.column_hidden_vectors] = np.concatenate(
                scaled_numeric_column_names, 1)  # shape 20 x 40 x 100
            scaled_feed[graph.word_column_hidden_vectors] = np.concatenate(
                scaled_word_column_names, 1)  # shape 20 x 40

            # compute gradients
            fetches = [graph.final_operation_softmax, graph.final_column_softmax,
                       graph.operator_gradients_default_program, graph.column_gradients_default_program]
            temp_op_softmax, temp_col_softmax, operator_gradients, column_gradients = sess.run(
                fetches, scaled_feed)  # operator gradient shape: 4 x 62 x 20 x 256

            attr_op_softmax.append(temp_op_softmax)
            attr_col_softmax.append(temp_col_softmax)

            # compute attributions
            for stage in range(graph.max_passes):
                n = int(len(operator_gradients) / graph.max_passes)
                temp = [np.sum(operator_gradients[n * stage][0][:, i, :] *
                               numeric_column_name_jump[i]) for i in range(graph.num_cols)]
                temp += [np.sum(operator_gradients[n * stage + 1][0][:, i, :] *
                                word_column_name_jump[i]) for i in range(graph.num_word_cols)]
                batch_op_attribution[stage, :] += temp

            for stage in range(graph.max_passes):
                n = int(len(column_gradients) / graph.max_passes)
                temp = [np.sum(column_gradients[n * stage][0][:, i, :] *
                               numeric_column_name_jump[i]) for i in range(graph.num_cols)]
                temp += [np.sum(column_gradients[n * stage + 1][0][:, i, :] *
                                word_column_name_jump[i]) for i in range(graph.num_word_cols)]
                batch_col_attribution[stage, :] += temp

        # sanity check
        attr_op_softmax = np.concatenate(attr_op_softmax, axis=0)
        attr_col_softmax = np.concatenate(attr_col_softmax, axis=0)
        for stage in range(graph.max_passes):
            lhs = np.sum(batch_op_attribution[stage, :])
            input_fn_value = operation_softmax[batch_id,
                                               stage, op_indices[stage]]
            baseline_fn_value = attr_op_softmax[0, stage, op_indices[stage]]
            rhs = input_fn_value - baseline_fn_value
            print('OP', stage, ':', 'baseline=', baseline_fn_value, ', input_fn=', input_fn_value, 'check: ', lhs, ' - ', rhs, ' = ', lhs - rhs)
        for stage in range(graph.max_passes):
            lhs = np.sum(batch_col_attribution[stage, :])
            input_fn_value = column_softmax[batch_id,
                                            stage, col_indices[stage]]
            baseline_fn_value = attr_col_softmax[0, stage, col_indices[stage]]
            rhs = input_fn_value - baseline_fn_value
            print('COL', stage, ':', 'baseline=', baseline_fn_value, ', input_fn=', input_fn_value, 'check: ', lhs, ' - ', rhs, ' = ', lhs - rhs)

        op_attributions = [None]*graph.max_passes

        attributions_matrix = np.zeros(
            [actual_num_numeric_cols + actual_num_word_cols, 2 * graph.max_passes])
        
        row_labels = []  # column headers
        col_labels = []  # operator and column selections
        col_label_softmaxes = []  # softmaxes of the selections

        for i in range(actual_num_numeric_cols):
            word = utility.reverse_word_ids[wiki_example.column_ids[i][0]]
            row_labels.append(word)
            
        for i in range(actual_num_word_cols):
            word = utility.reverse_word_ids[wiki_example.word_column_ids[i][0]]
            row_labels.append(word)

        non_dummy_indices = np.arange(actual_num_numeric_cols).tolist() + (np.arange(actual_num_word_cols) + graph.num_cols).tolist()
        for stage in range(graph.max_passes):
            col_labels.append(notebook_utils.rename(
                op_list[stage]) + ' (' + notebook_utils.rename(default_op_list[stage]) + ')')
            col_labels.append(notebook_utils.rename(
                col_list[stage]) + ' (' + notebook_utils.rename(default_col_list[stage]) + ')')

            col_label_softmaxes.append(str(operation_softmax[batch_id, stage, op_indices[stage]]) + ' (' + str(
                default_operation_softmax[batch_id, stage, op_indices[stage]]) + ')')
            col_label_softmaxes.append(str(column_softmax[batch_id, stage, col_indices[stage]]) + ' (' + str(
                default_column_softmax[batch_id, stage, col_indices[stage]]) + ')')

            attributions_matrix[:, 2 * stage] = batch_op_attribution[stage, non_dummy_indices]
            attributions_matrix[:, 2 * stage +
                                1] = batch_col_attribution[stage, non_dummy_indices]

        # save operator and column selections to file
        with tf.gfile.GFile(os.path.join(attrs_outdir, notebook_utils.process_table_key(wiki_example.table_key) + '_labels.tsv'), 'w') as outf:
            outf.write('\t'.join(row_labels) + '\n')
            outf.write('\t'.join(col_labels) + '\n')
            outf.write('\t'.join(col_label_softmaxes) + '\n')

        # save attributions to file
        np.savetxt(os.path.join(
            attrs_outdir, notebook_utils.process_table_key(wiki_example.table_key) + '_attrs.txt'), attributions_matrix)

['reset', 'reset', 'max', 'print']
['wins', 'wins', 'wins', 'county']
k: 0
k: 20
k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.9950289895657871 check:  0.6739931  -  

k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.9983013953642534 check:  0.6771049  -  0.6771846067882746  =  -7.97164417475349e-05
OP 2 : baseline= 0.49813370741661056 , input_fn= 0.6759739120839834 check:  0.17788258  -  0.17784020466737283  =  4.237728186118339e-05
OP 3 : baseline= 0.9739790395278459 , input_fn= 0.9915927362240832 check:  0.017620703  -  0.017613696696237247  =  7.006509229023905e-06
COL 0 : baseline= 0.14285714285714285 , input_fn= 0.9833607840830636 check:  0.8406722  -  0.8405036412259208  =  0.00016855373181234867
COL 1 : baseline= 0.14285714285714285 , input_fn= 0.9953420397179896 check:  0.8525968  -  0.8524848968608467  =  0.00011192253994063428
COL 2 : baseline= 0.14285714285714285 , input_fn= 0.6299192788551007 check:  0.48701912  -  0.48706213599795783  =  -4.301435107673113e-05
COL 3 : baseline= 0.14285714285714285 , input_fn= 0.9994355134287

k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.36970860351061186 , input_fn= 0.9667344142459355 check:  0.5971803  -  0.5970258107353237  =  0.00015449617614482491
OP 2 : baseline= 0.498133707416610

k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.9916115827847616 check:  0.67053926  -  0.6704947942087828  =  4.446570180072218e-05
OP 2 : baseline= 0.49813370741661056 , input_fn= 0.5050597521417275 check:  0.007014582  -  0.006926044725116931  =  8.853720850066082e-05
OP 3 : baseline= 0.9739790395278459 , input_fn= 0.6906753784864862 check:  -0.28322306  -  -0.28330366104135973  =  8.059828768236521e-05
COL 0 : baseline= 0.2 , input_fn= 0.5375271729623339 check:  0.3375431  -  0.33752717296233387  =  1.592715630321928e-05
COL 1 : baseline= 0.2 , input_fn= 0.7387533321589174 check:  0.53871983  -  0.5387533321589173  =  -3.349926173101814e-05
COL 2 : baseline= 0.2 , input_fn= 0.4346462049955632 check:  0.23473667  -  0.2346462049955632  =  9.046108777266415e-05
COL 3 : baseline= 0.2 , input_fn= 0.9952002020566566 check:  0.7957246  -  0.7952002020566566  =  0.00052436869

k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.4470065978021761 check:  0.1257645  -  0.1258898092261973  =  -0.0001253051511469483
OP 2 : baseline= 0.4981337074166105

...

k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.9810517262036388 check:  0.6599517  -  0.65993493762766  =  1.6749231470880588e-05
OP 2 : baseline= 0.07441098961237361 , input_fn= 0.46242625105404717 check:  0.38792312  -  0.38801526144167353  =  -9.21399893419883e-05
OP 3 : baseline= 0.9739790395278459 , input_fn= 0.6499250569390946 check:  -0.32392597  -  -0.3240539825887513  =  0.0001280106038880069
COL 0 : baseline= 0.07142857142857142 , input_fn= 0.5589386727679433 check:  0.48751757  -  0.4875101013393719  =  7.464149443414669e-06
COL 1 : baseline= 0.07142857142857142 , input_fn= 0.6236322852138612 check:  0.5522489  -  0.5522037137852898  =  4.5181383014680776e-05
COL 2 : baseline= 0.07142857142857142 , input_fn= 0.23474349031992717 check:  0.16327891  -  0.16331491889135574  =  -3.601135389541543e-05
COL 3 : baseline= 0.07142857142857142 , i

k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.993298746525932 check:  0.672189  -  0.6721819579499532  =  7.039318723589538e-06
OP 2 : baseline= 0.11390357718815533 ,

k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.09017920745046028 , input_fn= 0.5749328237774377 check:  0.48473656  -  0.48475361632697744  =  -1.7054551769923876e-05
OP 2 : baseline= 0.498133707416

k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.9766211594407191 check:  0.6555434  -  0.6555043708647403  =  3.9016071447406375e-05
OP 2 : baseline= 0.49813370741661056 , input_fn= 0.5764286673139666 check:  0.078135855  -  0.07829495989735602  =  -0.0001591044014263021
OP 3 : baseline= 0.9739790395278459 , input_fn= 0.9994253502457522 check:  0.025465488  -  0.025446310717906262  =  1.9177715931628647e-05
COL 0 : baseline= 0.25 , input_fn= 0.7581939126972793 check:  0.50821257  -  0.5081939126972793  =  1.8653678453106615e-05
COL 1 : baseline= 0.25 , input_fn= 0.9244168893288449 check:  0.67444956  -  0.6744168893288449  =  3.2673697583307515e-05
COL 2 : baseline= 0.25 , input_fn= 0.9679126433423427 check:  0.7180239  -  0.7179126433423427  =  0.0001112528750034647
COL 3 : baseline= 0.25 , input_fn= 0.4093030470109823 check:  0.159

k: 40
k: 60
k: 80
k: 100
k: 120
k: 140
k: 160
k: 180
k: 200
k: 220
k: 240
k: 260
k: 280
k: 300
k: 320
k: 340
k: 360
k: 380
k: 400
k: 420
k: 440
k: 460
k: 480
k: 500
k: 520
k: 540
k: 560
k: 580
k: 600
k: 620
k: 640
k: 660
k: 680
k: 700
k: 720
k: 740
k: 760
k: 780
k: 800
k: 820
k: 840
k: 860
k: 880
k: 900
k: 920
k: 940
k: 960
k: 980
k: 1000
k: 1020
k: 1040
k: 1060
k: 1080
k: 1100
k: 1120
k: 1140
k: 1160
k: 1180
k: 1200
k: 1220
k: 1240
k: 1260
k: 1280
k: 1300
k: 1320
k: 1340
k: 1360
k: 1380
k: 1400
k: 1420
k: 1440
k: 1460
k: 1480
k: 1500
k: 1520
k: 1540
k: 1560
k: 1580
k: 1600
k: 1620
k: 1640
k: 1660
k: 1680
k: 1700
k: 1720
k: 1740
k: 1760
k: 1780
k: 1800
k: 1820
k: 1840
k: 1860
k: 1880
k: 1900
k: 1920
k: 1940
k: 1960
k: 1980
OP 0 : baseline= 0.41344064754127735 , input_fn= 0.41344064754127735 check:  0.0  -  0.0  =  0.0
OP 1 : baseline= 0.3211167885759788 , input_fn= 0.8204408191555346 check:  0.49924505  -  0.49932403057955577  =  -7.898301028086419e-05
OP 2 : baseline= 0.49813370741661

### Common triggers for table-specific default program operators

In [114]:
data = list(unique_tables.values())

In [138]:
program_triggers = defaultdict(lambda: [])
program_counts = defaultdict(int)
for wiki_example in data[:graph.batch_size*int(len(data)/graph.batch_size)]:
    with tf.gfile.GFile(os.path.join(attrs_outdir, notebook_utils.process_table_key(wiki_example.table_key) + '_labels.tsv')) as f:
        row_labels = f.readline().strip().split('\t')
        col_labels = f.readline().strip().split('\t')
        
    attrs = np.loadtxt(os.path.join(
            attrs_outdir, notebook_utils.process_table_key(wiki_example.table_key) + '_attrs.txt'))
    
    synonyms = []
    for i, stage in enumerate(col_labels):
        synonyms.append(row_labels[np.argmax(attrs[:, i])])
    
    program = ' '.join([c.split()[0] for i, c in enumerate(col_labels) if i%2 == 0])
    program_triggers[program] = program_triggers[program] + synonyms       
    program_counts[program] += 1

In [140]:
K = 10
df_data = []
for program, triggers in program_triggers.items():
    topk = Counter(triggers).most_common(K)
    df_data.append([program, [w for w, _ in topk]])
sorted(df_data, key=operator.itemgetter(1), reverse=True)
pd.DataFrame(df_data, columns=['operator sequence', 'triggers'])

operator sequence  \
0       reset reset max print   
1        reset prev max print   
2       reset reset min print   
3      reset next first print   
4     reset reset reset print   
5       reset mfe first print   
6        reset mfe last print   
7     reset reset first print   
8     reset select last print   
9         reset mfe max print   
10       reset prev min print   
11     reset reset last print   
12     reset prev first print   
13       reset next max print   
14      reset prev last print   
15  reset select select print   
16    reset reset first count   
17     reset reset last count   
18      reset next last print   
19     reset mfe select print   

                                             triggers  
0   [points, competition, UNK, year, name, notes, ...  
1   [total, bronze, UNK, rank, no, year, nation, n...  
2   [height, jan, floors, single, name, age, month...  
3   [edition, UNK, urban, definition, name, birth,...  
4                   [candidates, district, incumbent]  
5   [genre, title, year, partner, notes, region, f...  
6   [tier, UNK, season, works, note, rank, positio...  
7   [rank, comments, previous, nationality, UNK, n...  
8        [finish, coordinates, UNK, laps, start, car]  
9   [opponent, name, date, rank, attendance, year,...  
10  [movements, level, joined, works, gauge, seaso...  
11  [distance, certifications, loss, goal, year, u...  
12  [kilometers, athlete, serial, rank, constituen...  
13                                   [UNK, ethnicity]  
14  [report, east, works, candidate, season, name,...  
15                                   [lifetime, name]  
16                        [programming, UNK, network]  
17                        [japanese, year, UNK, type]  
18                                     [comment, UNK]  
19          [producer, title, UNK, length, performer]

## Accuracy on perturbed tables
- Perturbed data is arranged such that unperturbed questions appear before perturbed questions. This results in words being added in the same order to the vocab (to effect in same word IDs) as in the unperturbed case.
- Since the vocabulary has more words in the perturbed case (due to some words exceeding the min cutoff), special words such as `unk_token` are assigned different IDs. We revert this by swapping word IDs appropriately. The goal being that the word IDs of words in perturbed case should be the same as word IDs of words in the unperturbed case. This is done in `notebook_utils.init_data()` using the argument `preserve_vocab` (default value is `False`)

In [14]:
perturbed_train_data, perturbed_dev_data, perturbed_test_data, perturbed_utility = notebook_utils.init_data(PERTURBED_DATA_DIR, preserve_vocab=True)

('Annotated examples loaded ', 58141)
('Annotated examples loaded ', 4344)
('entry match token: ', 9169, 9169)
('entry match token: ', 9170, 9170)
hardcoded ids for special words
9133 9134 9135 9136
('# train examples ', 43835)
('# dev examples ', 10994)
('# test examples ', 3913)


In [15]:
perturbed_correct, perturbed_num_examples, perturbed_correct_dict = evaluate(sess, perturbed_dev_data, perturbed_utility.FLAGS.batch_size, graph, model_step)

('dev set accuracy   after ', 92500, ' : ', 0.2556773688332028)
(2554, 10994)
--------


In [17]:
perturbed_correct/2831

0.23066054397739313

## Question concatenation attacks

In [61]:
ATTACK_PHRASES = [
    'in not a lot of words',
    'in this chart',
    'among these rows listed',
    'if its all the same',
    'above all',
    'at the moment'
]    

In [90]:
num_correct_list = []
for phrase in ATTACK_PHRASES:
    prefix_correct, _, _ = notebook_utils.evaluate_concatenation_attack(sess, dev_data, graph.batch_size, graph, model_step, utility, phrase, suffix=False)
    suffix_correct, _, _ = notebook_utils.evaluate_concatenation_attack(sess, dev_data, graph.batch_size, graph, model_step, utility, phrase, suffix=True)
    num_correct_list.append([prefix_correct, suffix_correct])

[21, 810, 8, 9136, 10, 9136]
('dev set accuracy   after ', 92500, ' : ', 0.2608012568735271)
(2546, 2546)
--------
[21, 810, 8, 9136, 10, 9136]
('dev set accuracy   after ', 92500, ' : ', 0.13825608798114689)
(2546, 2546)
--------
[21, 6, 59]
('dev set accuracy   after ', 92500, ' : ', 0.3605655930871956)
(2546, 2546)
--------
[21, 6, 59]
('dev set accuracy   after ', 92500, ' : ', 0.35742340926944227)
(2546, 2546)
--------
[9136, 518, 9136, 125]
('dev set accuracy   after ', 92500, ' : ', 0.36252945797329145)
(2546, 2546)
--------
[9136, 518, 9136, 125]
('dev set accuracy   after ', 92500, ' : ', 0.35467399842890807)
(2546, 2546)
--------
[550, 1093, 284, 2, 630]
('dev set accuracy   after ', 92500, ' : ', 0.27808326787117044)
(2546, 2546)
--------
[550, 1093, 284, 2, 630]
('dev set accuracy   after ', 92500, ' : ', 0.24234092694422624)
(2546, 2546)
--------
[510, 284]
('dev set accuracy   after ', 92500, ' : ', 0.31382560879811466)
(2546, 2546)
--------
[510, 284]
('dev set accuracy 

In [91]:
pd.DataFrame(np.concatenate([np.expand_dims(ATTACK_PHRASES,1), np.array(num_correct_list)/2831], axis=1), columns=['attack phrase', 'prefix acc.','suffix acc.'])

attack phrase          prefix acc.          suffix acc.
0    in not a lot of words  0.23454609678558813  0.12433768986223949
1            in this chart  0.32426704344754503  0.32144118685976686
2  among these rows listed   0.3260332038149064  0.31896856234546095
3      if its all the same  0.25008830801836807  0.21794418933239137
4                above all  0.28223242670434473   0.2264217590957259
5            at the moment  0.32921229247615685   0.2998940303779583

## Stop word deletion attack

In [14]:
all_words = [wiki_example.string_question for wiki_example in dev_data]
all_words = [x for y in all_words for x in y]

In [29]:
nltk.download('stopwords')
STOP_WORDS = set(nltk.corpus.stopwords.words('english'))

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/pramodkm/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [30]:
STOP_WORDS

{'a',
 'about',
 'above',
 'after',
 'again',
 'against',
 'ain',
 'all',
 'am',
 'an',
 'and',
 'any',
 'are',
 'aren',
 "aren't",
 'as',
 'at',
 'be',
 'because',
 'been',
 'before',
 'being',
 'below',
 'between',
 'both',
 'but',
 'by',
 'can',
 'couldn',
 "couldn't",
 'd',
 'did',
 'didn',
 "didn't",
 'do',
 'does',
 'doesn',
 "doesn't",
 'doing',
 'don',
 "don't",
 'down',
 'during',
 'each',
 'few',
 'for',
 'from',
 'further',
 'had',
 'hadn',
 "hadn't",
 'has',
 'hasn',
 "hasn't",
 'have',
 'haven',
 "haven't",
 'having',
 'he',
 'her',
 'here',
 'hers',
 'herself',
 'him',
 'himself',
 'his',
 'how',
 'i',
 'if',
 'in',
 'into',
 'is',
 'isn',
 "isn't",
 'it',
 "it's",
 'its',
 'itself',
 'just',
 'll',
 'm',
 'ma',
 'me',
 'mightn',
 "mightn't",
 'more',
 'most',
 'mustn',
 "mustn't",
 'my',
 'myself',
 'needn',
 "needn't",
 'no',
 'nor',
 'not',
 'now',
 'o',
 'of',
 'off',
 'on',
 'once',
 'only',
 'or',
 'other',
 'our',
 'ours',
 'ourselves',
 'out',
 'over',
 'own',
 'r

In [18]:
STOP_WORDS = """ the, or, show,  tell, did,  me,  my, our,  are,  is,
        were, this, on, would, and,  for, should,  be, 
        do, I, have, had, the,  there,  look, give, 
        has,  was, we, get, does, a,  an,  's,  that,  
        by,  based on, in,  of, bring,  with, to, from, 
        whole, being, been,  want, wanted, as, can, 
        see, doing, got, sorted, draw, listed, chart, only"""
STOP_WORDS = STOP_WORDS.strip().split(', ')
stop_word_ids = set([utility.word_ids[w] for w in STOP_WORDS if w in utility.word_ids])
question_attention_mask_value = -10000

In [19]:
stop_word_data = copy.deepcopy(dev_data)
for i, wiki_example in enumerate(stop_word_data):
    new_question = []
    new_question_mask = []
    for w in wiki_example.question:
        if w not in stop_word_ids and w != utility.dummy_token_id:
            new_question.append(w)
            new_question_mask.append(0)
                
    stop_word_data[i].question = [utility.dummy_token_id] * (graph.question_length - len(new_question)) + new_question

    stop_word_data[i].question_attention_mask = [question_attention_mask_value] * (graph.question_length - len(new_question_mask)) + new_question_mask

In [20]:
num_correct, _, _ = evaluate(sess, stop_word_data, graph.batch_size, graph, model_step)

('dev set accuracy   after ', 92500, ' : ', 0.3487824037706206)
(2546, 2546)
--------


In [21]:
num_correct/2831

0.3136700812433769

## Overstability analysis

In [32]:
data = dev_data

In [38]:
frequent_attributions = []
for wiki_example in data[:graph.batch_size*int(len(data)/graph.batch_size)]:
    with tf.gfile.GFile(os.path.join(attrs_outdir, wiki_example.question_id + '_labels.tsv')) as f:
        f.readline()
        f.readline()
        row_labels = f.readline().strip().split('\t')
        col_labels = f.readline().strip().split('\t')
        
    attrs = np.loadtxt(os.path.join(
            attrs_outdir, wiki_example.question_id + '_attrs.txt'))
    
    synonyms = []
    for i, stage in enumerate(col_labels):
        synonyms.append(row_labels[np.argmax(attrs[:, i])])
    
    frequent_attributions.extend(synonyms)


In [44]:
Counter(frequent_attributions).most_common(20)

[('tm', 4640),
 ('cm', 3476),
 ('many', 1788),
 ('tm_token', 1151),
 ('number', 763),
 ('total', 394),
 ('after', 359),
 ('most', 335),
 ('or', 328),
 ('how', 324),
 ('last', 319),
 ('least', 307),
 ('who', 265),
 ('before', 265),
 ('first', 260),
 ('cm_token', 247),
 ('top', 165),
 ('long', 159),
 ('than', 152),
 ('difference', 152)]

In [ ]:
utility.word_ids['tm_token'] = utility.entry_match_token_id
utility.word_ids['cm_token'] = utility.column_match_token_id
curve_data = {}
for K in np.unique(np.floor(np.geomspace(3, len(Counter(frequent_attributions)), 25))):
    if int(K) in curve_data:
        continue
    whitelist = set([w for w, _ in Counter(frequent_attributions).most_common(int(K))[2:]]) # 2: to exclude tm, cm bias
    whitelist = set([utility.word_ids[w] for w in whitelist])
    
    reduced_vocab_data = copy.deepcopy(dev_data)
    for i, wiki_example in enumerate(reduced_vocab_data):
        new_question = []
        for w in wiki_example.question:
            if w in whitelist:
                new_question.append(w)
        reduced_vocab_data[i].question = [utility.dummy_token_id] * (graph.question_length - len(new_question)) + new_question
        reduced_vocab_data[i].question_attention_mask = [question_attention_mask_value] * (graph.question_length - len(new_question)) + [0] * len(new_question)
    
    num_correct, _, _ = evaluate(sess, reduced_vocab_data, graph.batch_size, graph, model_step)
    curve_data[int(K)] = num_correct
    print(int(K), num_correct)
        

In [ ]:
plt.plot(curve_data.keys(), np.divide(curve_data.values(), 2831))
plt.xscale('log')
plt.xlabel('num. words in vocab')
plt.ylabel('accuracy')
plt.savefig(OVERSTABILITY_CURVE_FILE, format='eps')
plt.show()